# User-Based Collaborative Filtering

* Create User Movie DataFrame
* Determining the movies watched by the user to be recommended
* Find other users watching the same movies
* Determination of Similarity
* Calculate Weighted Average Recommendation Score
* Process Functionalization

# Import Necessary Libraries

In [1]:
import numpy as np
import pandas as pd
pd.set_option("display.max_columns",None)
pd.set_option("display.max_rows",None)
pd.set_option("display.width",500)
pd.set_option("display.expand_frame_repr",False)

# Import Dataset

In [2]:
movies = pd.read_csv("movies.csv")
ratings = pd.read_csv("ratings.csv")
df = movies.merge(ratings, how="left", on="movieId")
df.head()

movieId             title                                       genres  userId  rating     timestamp
0        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy     3.0     4.0  9.449194e+08
1        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy     6.0     5.0  8.582755e+08
2        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy     8.0     4.0  8.339819e+08
3        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy    10.0     4.0  9.434979e+08
4        1  Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy    11.0     4.5  1.230859e+09

# Create User Movie DataFrame

In [3]:
df.shape 

(20000797, 6)

In [4]:
df["title"].nunique()

27262

In [5]:
df["title"].value_counts().head() 

Pulp Fiction (1994)                 67310
Forrest Gump (1994)                 66172
Shawshank Redemption, The (1994)    63366
Silence of the Lambs, The (1991)    63299
Jurassic Park (1993)                59715
Name: title, dtype: int64

In [6]:
rating_counts = pd.DataFrame(df["title"].value_counts())

In [7]:
rating_counts.head()

title
Pulp Fiction (1994)               67310
Forrest Gump (1994)               66172
Shawshank Redemption, The (1994)  63366
Silence of the Lambs, The (1991)  63299
Jurassic Park (1993)              59715

In [8]:
rating_counts[rating_counts["title"] < 1000].head()

title
Bear, The (Ours, L') (1988)     999
Rosewood (1997)                 999
Ted (2012)                      999
One Night at McCool's (2001)    999
Marked for Death (1990)         998

In [9]:
rating_counts[rating_counts["title"] < 1000].shape # 24 bin filimin yorumu ve beğenisi 1000 altında

(24103, 1)

In [10]:
rare_movies = rating_counts[rating_counts["title"] < 1000].index

In [11]:
rare_movies[0:5]

Index(['Bear, The (Ours, L') (1988)', 'Rosewood (1997)', 'Ted (2012)', 'One Night at McCool's (2001)', 'Marked for Death (1990)'], dtype='object')

In [12]:
common_movies = df[~df["title"].isin(rare_movies)]

In [13]:
common_movies.shape

(17766015, 6)

In [14]:
df.shape

(20000797, 6)

In [15]:
common_movies["title"].nunique()

3159

In [16]:
df["title"].nunique() 

27262

In [17]:
user_movie_df = common_movies.pivot_table(index=["userId"], columns=["title"], values="rating")

In [18]:
user_movie_df.shape

(138493, 3159)

# Determining the movies watched by the user to be recommended


In [19]:
random_user = int(pd.Series(user_movie_df.index).sample(1, random_state=50).values)
random_user

80107

In [20]:
random_user_df = user_movie_df[user_movie_df.index == random_user]

In [21]:
random_user_df

title    'burbs, The (1989)  (500) Days of Summer (2009)  *batteries not included (1987)  ...And Justice for All (1979)  10 Things I Hate About You (1999)  10,000 BC (2008)  101 Dalmatians (1996)  101 Dalmatians (One Hundred and One Dalmatians) (1961)  102 Dalmatians (2000)  12 Angry Men (1957)  12 Years a Slave (2013)  127 Hours (2010)  13 Going on 30 (2004)  13th Warrior, The (1999)  1408 (2007)  15 Minutes (2001)  16 Blocks (2006)  17 Again (2009)  1984 (Nineteen Eighty-Four) (1984)  2 Days in the Valley (1996)  2 Fast 2 Furious (Fast and the Furious 2, The) (2003)  20,000 Leagues Under the Sea (1954)  200 Cigarettes (1999)  2001: A Space Odyssey (1968)  2010: The Year We Make Contact (1984)  2012 (2009)  2046 (2004)  21 (2008)  21 Grams (2003)  21 Jump Street (2012)  24 Hour Party People (2002)  25th Hour (2002)  27 Dresses (2008)  28 Days (2000)  28 Days Later (2002)  28 Weeks Later (2007)  3 Ninjas (1992)  3-Iron (Bin-jip) (2004)  30 Days of Night (2007)  300 (2007)  3000 Miles to Graceland (2001)  39 Steps, The (1935)  3:10 to Yuma (2007)  40 Days and 40 Nights (2002)  40-Year-Old Virgin, The (2005)  400 Blows, The (Les quatre cents coups) (1959)  42 Up (1998)  48 Hrs. (1982)  50 First Dates (2004)  50/50 (2011)  54 (1998)  6th Day, The (2000)  7th Voyage of Sinbad, The (1958)  8 1/2 (8½) (1963)  8 Heads in a Duffel Bag (1997)  8 Mile (2002)  8MM (1999)  9 (2009)  9 1/2 Weeks (Nine 1/2 Weeks) (1986)  A-Team, The (2010)  A.I. Artificial Intelligence (2001)  AVP: Alien vs. Predator (2004)  AVPR: Aliens vs. Predator - Requiem (2007)  About Last Night... (1986)  About Schmidt (2002)  About a Boy (2002)  Absent-Minded Professor, The (1961)  Absolute Power (1997)  Abyss, The (1989)  Accepted (2006)  Accidental Tourist, The (1988)  Accused, The (1988)  Ace Ventura: Pet Detective (1994)  Ace Ventura: When Nature Calls (1995)  Across the Universe (2007)  Adaptation (2002)  Addams Family Values (1993)  Addams Family, The (1991)  Addicted to Love (1997)  Adjustment Bureau, The (2011)  Adventureland (2009)  Adventures in Babysitting (1987)  Adventures of Baron Munchausen, The (1988)  Adventures of Buckaroo Banzai Across the 8th Dimension, The (1984)  Adventures of Milo and Otis, The (Koneko monogatari) (1986)  Adventures of Pinocchio, The (1996)  Adventures of Priscilla, Queen of the Desert, The (1994)  Adventures of Robin Hood, The (1938)  Adventures of Rocky and Bullwinkle, The (2000)  Adventures of Tintin, The (2011)  Aeon Flux (2005)  Affair to Remember, An (1957)  Affliction (1997)  African Queen, The (1951)  After Hours (1985)  Age of Innocence, The (1993)  Agnes of God (1985)  Aguirre: The Wrath of God (Aguirre, der Zorn Gottes) (1972)  Air America (1990)  Air Bud (1997)  Air Force One (1997)  Airheads (1994)  Airplane II: The Sequel (1982)  Airplane! (1980)  Airport (1970)  Akira (1988)  Aladdin (1992)  Aladdin and the King of Thieves (1996)  Alexander (2004)  Alfie (2004)  Ali (2001)  Alice in Wonderland (1951)  Alice in Wonderland (2010)  Alien (1979)  Alien Nation (1988)  Alien: Resurrection (1997)  Aliens (1986)  Alien³ (a.k.a. Alien 3) (1992)  Alive (1993)  All About Eve (1950)  All About My Mother (Todo sobre mi madre) (1999)  All Dogs Go to Heaven (1989)  All Dogs Go to Heaven 2 (1996)  All Quiet on the Western Front (1930)  All That Jazz (1979)  All the President's Men (1976)  All the Pretty Horses (2000)  Almost Famous (2000)  Along Came Polly (2004)  Along Came a Spider (2001)  Alphaville (Alphaville, une étrange aventure de Lemmy Caution) (1965)  Altered States (1980)  Always (1989)  Amadeus (1984)  Amateur (1994)  Amazing Spider-Man, The (2012)  Amelie (Fabuleux destin d'Amélie Poulain, Le) (2001)  America's Sweethearts (2001)  American Beauty (1999)  American Gangster (2007)  American Gigolo (1980)  American Graffiti (1973)  American History X (1998)  American Hustle (2013)  American Movie (1999)  American Pie (1999)  American Pie 2 (2001)  American President, The (1995)  American Psycho (2000)  American Splend

In [22]:

movies_wtached = random_user_df.columns[random_user_df.notna().any()].tolist()

In [23]:
movies_wtached

['Apollo 13 (1995)',
 'Batman (1989)',
 'Beauty and the Beast (1991)',
 'Beverly Hills Cop III (1994)',
 'Braveheart (1995)',
 'Casper (1995)',
 'Cliffhanger (1993)',
 'Dances with Wolves (1990)',
 'Firm, The (1993)',
 'First Knight (1995)',
 'Forrest Gump (1994)',
 'Fugitive, The (1993)',
 'GoldenEye (1995)',
 'Interview with the Vampire: The Vampire Chronicles (1994)',
 'Johnny Mnemonic (1995)',
 'Judge Dredd (1995)',
 'Jumanji (1995)',
 'Jurassic Park (1993)',
 'Lion King, The (1994)',
 'Mask, The (1994)',
 'Natural Born Killers (1994)',
 'Pocahontas (1995)',
 'Silence of the Lambs, The (1991)',
 'Star Trek: Generations (1994)',
 'Taxi Driver (1976)',
 'True Lies (1994)',
 'Waterworld (1995)']

In [24]:
user_movie_df.loc[user_movie_df.index == random_user, user_movie_df.columns == "Taxi Driver (1976)"]

title    Taxi Driver (1976)
userId                     
80107.0                 3.0

In [25]:
user_movie_df.loc[user_movie_df.index == random_user, user_movie_df.columns == "Apollo 13 (1995)"]

title    Apollo 13 (1995)
userId                   
80107.0               4.0

In [26]:
len(movies_wtached) 

27

# Find other users watching the same movies

Aynı filmleri izleyen diğer kullanıcıları bulmak

In [27]:
movies_watched_df = user_movie_df[movies_wtached]

In [28]:
movies_watched_df.head()

title   Apollo 13 (1995)  Batman (1989)  Beauty and the Beast (1991)  Beverly Hills Cop III (1994)  Braveheart (1995)  Casper (1995)  Cliffhanger (1993)  Dances with Wolves (1990)  Firm, The (1993)  First Knight (1995)  Forrest Gump (1994)  Fugitive, The (1993)  GoldenEye (1995)  Interview with the Vampire: The Vampire Chronicles (1994)  Johnny Mnemonic (1995)  Judge Dredd (1995)  Jumanji (1995)  Jurassic Park (1993)  Lion King, The (1994)  Mask, The (1994)  Natural Born Killers (1994)  Pocahontas (1995)  Silence of the Lambs, The (1991)  Star Trek: Generations (1994)  Taxi Driver (1976)  True Lies (1994)  Waterworld (1995)
userId                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
1.0                  NaN            NaN                          NaN                           NaN                NaN            NaN                 NaN                        NaN               NaN                  NaN                  NaN                   NaN               NaN                                                4.0                             NaN                 NaN             3.5                   NaN                    NaN               3.5                          NaN                NaN                               3.5                            NaN                 NaN               NaN                NaN
2.0                  NaN            NaN                          NaN                           NaN                4.0            NaN                 NaN                        NaN               NaN                  NaN                  NaN                   NaN               NaN                                                NaN                             NaN                 NaN             NaN                   5.0                    NaN               NaN                          NaN                NaN                               NaN                            NaN                 NaN               NaN                NaN
3.0                  NaN            NaN                          NaN                           NaN                NaN            NaN                 NaN                        NaN               NaN                  NaN                  NaN                   5.0               NaN                                                NaN                             NaN                 2.0             NaN                   5.0                    NaN               NaN                          NaN                NaN                               5.0                            5.0                 NaN               NaN                NaN
4.0                  NaN            NaN                          NaN                           3.0                NaN            NaN                 NaN                        NaN               5.0                  NaN                  4.0                   NaN               4.0                                                NaN                             NaN                 NaN             NaN                   4.0                    NaN               3.0                          NaN                NaN                               NaN                            3.0                 NaN               3.0                NaN
5.0                  5.0            NaN                          5.0                           NaN                4.0            NaN                 NaN                        5.0               5.0           

In [29]:
movies_watched_df.shape

(138493, 27)

In [30]:
user_movie_count = movies_watched_df.T.notnull().sum()

In [31]:
user_movie_count.head()

userId
1.0     4
2.0     2
3.0     5
4.0     8
5.0    12
dtype: int64

In [32]:
user_movie_count = user_movie_count.reset_index()
user_movie_count.columns = ["userId", "movie_count"]

In [33]:
user_movie_count.head()

userId  movie_count
0     1.0            4
1     2.0            2
2     3.0            5
3     4.0            8
4     5.0           12

In [34]:
user_movie_count[user_movie_count["movie_count"] > 20].sort_values(by="movie_count", ascending=False)

userId  movie_count
19953    19954.0           27
4528      4529.0           27
51373    51374.0           27
121542  121543.0           27
40482    40483.0           27
13169    13170.0           27
40284    40285.0           27
13063    13064.0           27
40166    40167.0           27
54446    54447.0           27
71974    71975.0           27
131960  131961.0           27
63439    63440.0           27
99230    99231.0           27
4593      4594.0           27
12617    12618.0           27
54458    54459.0           27
54464    54465.0           27
48289    48290.0           27
29574    29575.0           27
97729    97730.0           27
83089    83090.0           27
47988    47989.0           27
13937    13938.0           27
120574  120575.0           27
101109  101110.0           27
103653  103654.0           27
103596  103597.0           27
15365    15366.0           27
118753  118754.0           27
134351  134352.0           27
63256    63257.0           27
79698    79699.0           27
134137  134138.0           27
102704  102705.0           27
80106    80107.0           27
80184    80185.0           27
72982    72983.0           27
14704    14705.0           27
102037  102038.0           27
51557    51558.0           27
101164  101165.0           27
27238    27239.0           27
120270  120271.0           27
81217    81218.0           27
50932    50933.0           27
12130    12131.0           27
62761    62762.0           27
86274    86275.0           27
70341    70342.0           27
10320    10321.0           27
125040  125041.0           27
93112    93113.0           27
92955    92956.0           27
92615    92616.0           27
128119  128120.0           27
92010    92011.0           27
36152    36153.0           27
8923      8924.0           27
35833    35834.0           27
127400  127401.0           27
90137    90138.0           27
8583      8584.0           27
89688    89689.0           27
89568    89569.0           27
69792    69793.0           27
89306    89307.0           27
8404      8405.0           27
124576  124577.0           27
130018  130019.0           27
11899    11900.0           27
95148    95149.0           27
83827    83828.0           27
83958    83959.0           27
5622      5623.0           27
122939  122940.0           27
84009    84010.0           27
97140    97141.0           27
48676    48677.0           27
30514    30515.0           27
5813      5814.0           27
96858    96859.0           27
30589    30590.0           27
59872    59873.0           27
31658    31659.0           27
95550    95551.0           27
124051  124052.0           27
10915    10916.0           27
10905    10906.0           27
60158    60159.0           27
68955    68956.0           27
15485    15486.0           27
61167    61168.0           27
21663    21664.0           27
136267  136268.0           27
46662    46663.0           27
75447    75448.0           27
116316  116317.0           27
16937    16938.0           27
116453  116454.0           27
16864    16865.0           27
23842    23843.0           27
18814    18815.0           27
23876    23877.0           27
73614    73615.0           27
137685  137686.0           27
113631  113632.0           27
137838  137839.0           27
24218    24219.0           27
110757  110758.0           27
23298    23299.0           27
108247  108248.0           27
1279      1280.0           27
113990  113991.0           27
110643  110644.0           27
76629    76630.0           27
21901    21902.0           27
46469    46470.0           27
56916    56917.0           27
136679  136680.0           27
76436    76437.0           27
981        982.0           27
114752  114753.0           27
774        775.0           27
64241    64242.0           27
76068    76069.0           27
73610    73611.0           27
902        903.0           27
52115    52116.0           27
118253  118254.0           27
15918    15919.0           27
20456    20457.0           27
104945  104946.0    

In [35]:
user_movie_count[user_movie_count["movie_count"] > (len(movies_wtached)/2)+1].sort_values(by="movie_count", ascending=False)

userId  movie_count
104945  104946.0           27
13063    13064.0           27
54464    54465.0           27
96858    96859.0           27
62761    62762.0           27
981        982.0           27
68955    68956.0           27
23298    23299.0           27
81217    81218.0           27
114752  114753.0           27
95550    95551.0           27
116316  116317.0           27
36152    36153.0           27
23842    23843.0           27
23876    23877.0           27
8923      8924.0           27
116453  116454.0           27
95148    95149.0           27
24218    24219.0           27
130018  130019.0           27
13169    13170.0           27
56916    56917.0           27
97140    97141.0           27
54458    54459.0           27
113990  113991.0           27
69792    69793.0           27
99230    99231.0           27
40482    40483.0           27
112695  112696.0           27
112938  112939.0           27
40284    40285.0           27
21663    21664.0           27
40166    40167.0           27
70341    70342.0           27
21901    21902.0           27
8583      8584.0           27
774        775.0           27
79698    79699.0           27
97729    97730.0           27
113631  113632.0           27
131960  131961.0           27
80106    80107.0           27
54446    54447.0           27
902        903.0           27
80184    80185.0           27
10320    10321.0           27
5622      5623.0           27
10915    10916.0           27
125040  125041.0           27
59872    59873.0           27
121542  121543.0           27
64241    64242.0           27
89688    89689.0           27
89568    89569.0           27
60158    60159.0           27
2190      2191.0           27
86274    86275.0           27
89306    89307.0           27
31658    31659.0           27
118204  118205.0           27
61167    61168.0           27
63439    63440.0           27
63256    63257.0           27
29574    29575.0           27
122939  122940.0           27
124576  124577.0           27
13937    13938.0           27
30589    30590.0           27
124051  124052.0           27
90137    90138.0           27
27238    27239.0           27
120574  120575.0           27
65294    65295.0           27
118253  118254.0           27
14704    14705.0           27
25191    25192.0           27
1279      1280.0           27
93112    93113.0           27
128119  128120.0           27
35833    35834.0           27
92955    92956.0           27
92615    92616.0           27
118753  118754.0           27
83089    83090.0           27
127400  127401.0           27
59040    59041.0           27
83827    83828.0           27
92010    92011.0           27
120270  120271.0           27
83958    83959.0           27
5813      5814.0           27
84009    84010.0           27
10905    10906.0           27
30514    30515.0           27
19953    19954.0           27
46662    46663.0           27
12130    12131.0           27
110757  110758.0           27
103596  103597.0           27
134351  134352.0           27
103653  103654.0           27
76068    76069.0           27
110643  110644.0           27
51373    51374.0           27
137685  137686.0           27
50932    50933.0           27
108247  108248.0           27
46469    46470.0           27
136267  136268.0           27
102037  102038.0           27
11899    11900.0           27
48676    48677.0           27
106473  106474.0           27
4593      4594.0           27
101109  101110.0           27
51557    51558.0           27
101164  101165.0           27
48289    48290.0           27
137838  137839.0           27
52115    52116.0           27
73610    73611.0           27
8404      8405.0           27
76436    76437.0           27
15918    15919.0           27
136679  136680.0           27
16937    16938.0           27
4528      4529.0           27
102704  102705.0           27
75447    75448.0           27
18814    18815.0           27
76629    76630.0           27
20456    20457.0           27
71974    71975.0    

In [36]:
user_movie_count[user_movie_count["movie_count"] > (len(movies_wtached)*70)/100].sort_values(by="movie_count", ascending=False)

userId  movie_count
2190      2191.0           27
11899    11900.0           27
86274    86275.0           27
40166    40167.0           27
102037  102038.0           27
12617    12618.0           27
72982    72983.0           27
96858    96859.0           27
128119  128120.0           27
40284    40285.0           27
21901    21902.0           27
118204  118205.0           27
118253  118254.0           27
20456    20457.0           27
40482    40483.0           27
30589    30590.0           27
101164  101165.0           27
101109  101110.0           27
118753  118754.0           27
79698    79699.0           27
102704  102705.0           27
54446    54447.0           27
127400  127401.0           27
114752  114753.0           27
134351  134352.0           27
19953    19954.0           27
75447    75448.0           27
103653  103654.0           27
103596  103597.0           27
134137  134138.0           27
73614    73615.0           27
124051  124052.0           27
80184    80185.0           27
116316  116317.0           27
54464    54465.0           27
73610    73611.0           27
54458    54459.0           27
116453  116454.0           27
80106    80107.0           27
24218    24219.0           27
46662    46663.0           27
16937    16938.0           27
13937    13938.0           27
51557    51558.0           27
99230    99231.0           27
71974    71975.0           27
76436    76437.0           27
51373    51374.0           27
97729    97730.0           27
121542  121543.0           27
90137    90138.0           27
23842    23843.0           27
89306    89307.0           27
70341    70342.0           27
76629    76630.0           27
130018  130019.0           27
50932    50933.0           27
89568    89569.0           27
89688    89689.0           27
5622      5623.0           27
15918    15919.0           27
92010    92011.0           27
13169    13170.0           27
131960  131961.0           27
97140    97141.0           27
68955    68956.0           27
76068    76069.0           27
13063    13064.0           27
16864    16865.0           27
122939  122940.0           27
69792    69793.0           27
21663    21664.0           27
30514    30515.0           27
52115    52116.0           27
23876    23877.0           27
120270  120271.0           27
23298    23299.0           27
120574  120575.0           27
29574    29575.0           27
1279      1280.0           27
12130    12131.0           27
25191    25192.0           27
95550    95551.0           27
31658    31659.0           27
62761    62762.0           27
136679  136680.0           27
4593      4594.0           27
14704    14705.0           27
27238    27239.0           27
48289    48290.0           27
92615    92616.0           27
18814    18815.0           27
48676    48677.0           27
83827    83828.0           27
63256    63257.0           27
63439    63440.0           27
112695  112696.0           27
10905    10906.0           27
8923      8924.0           27
59040    59041.0           27
125040  125041.0           27
136267  136268.0           27
293        294.0           27
95148    95149.0           27
46469    46470.0           27
61167    61168.0           27
60158    60159.0           27
47988    47989.0           27
137838  137839.0           27
137685  137686.0           27
59872    59873.0           27
10320    10321.0           27
35833    35834.0           27
4528      4529.0           27
110643  110644.0           27
83089    83090.0           27
36152    36153.0           27
108247  108248.0           27
110757  110758.0           27
10915    10916.0           27
5813      5814.0           27
774        775.0           27
106473  106474.0           27
15485    15486.0           27
113990  113991.0           27
8404      8405.0           27
92955    92956.0           27
113631  113632.0           27
65294    65295.0           27
8583      8584.0           27
104945  104946.0           27
981        982.0           27
93112    93113.0    

In [37]:
user_movie_count[user_movie_count["movie_count"] == len(movies_wtached)].sort_values(by="movie_count", ascending=False)

userId  movie_count
293        294.0           27
93112    93113.0           27
89568    89569.0           27
89688    89689.0           27
90137    90138.0           27
92010    92011.0           27
92615    92616.0           27
92955    92956.0           27
95148    95149.0           27
86274    86275.0           27
95550    95551.0           27
96858    96859.0           27
97140    97141.0           27
97729    97730.0           27
99230    99231.0           27
101109  101110.0           27
89306    89307.0           27
84009    84010.0           27
102037  102038.0           27
76436    76437.0           27
71974    71975.0           27
72982    72983.0           27
73610    73611.0           27
73614    73615.0           27
75447    75448.0           27
76068    76069.0           27
76629    76630.0           27
83958    83959.0           27
79698    79699.0           27
80106    80107.0           27
80184    80185.0           27
81217    81218.0           27
83089    83090.0           27
83827    83828.0           27
101164  101165.0           27
102704  102705.0           27
774        775.0           27
128119  128120.0           27
121542  121543.0           27
122939  122940.0           27
124051  124052.0           27
124576  124577.0           27
125040  125041.0           27
127400  127401.0           27
130018  130019.0           27
120270  120271.0           27
131960  131961.0           27
134137  134138.0           27
134351  134352.0           27
136267  136268.0           27
136679  136680.0           27
137685  137686.0           27
120574  120575.0           27
118753  118754.0           27
103596  103597.0           27
112695  112696.0           27
103653  103654.0           27
104945  104946.0           27
106473  106474.0           27
108247  108248.0           27
110643  110644.0           27
110757  110758.0           27
112938  112939.0           27
118253  118254.0           27
113631  113632.0           27
113990  113991.0           27
114752  114753.0           27
116316  116317.0           27
116453  116454.0           27
118204  118205.0           27
70341    70342.0           27
69792    69793.0           27
68955    68956.0           27
16864    16865.0           27
13169    13170.0           27
13937    13938.0           27
14704    14705.0           27
15365    15366.0           27
15485    15486.0           27
15918    15919.0           27
16937    16938.0           27
12617    12618.0           27
18814    18815.0           27
19953    19954.0           27
20456    20457.0           27
21663    21664.0           27
21901    21902.0           27
23298    23299.0           27
13063    13064.0           27
12130    12131.0           27
65294    65295.0           27
5622      5623.0           27
902        903.0           27
981        982.0           27
1279      1280.0           27
2190      2191.0           27
4528      4529.0           27
4593      4594.0           27
5813      5814.0           27
11899    11900.0           27
8404      8405.0           27
8583      8584.0           27
8923      8924.0           27
10320    10321.0           27
10905    10906.0           27
10915    10916.0           27
23842    23843.0           27
23876    23877.0           27
24218    24219.0           27
59040    59041.0           27
51557    51558.0           27
52115    52116.0           27
54446    54447.0           27
54458    54459.0           27
54464    54465.0           27
56916    56917.0           27
59872    59873.0           27
25191    25192.0           27
60158    60159.0           27
61167    61168.0           27
62761    62762.0           27
63256    63257.0           27
63439    63440.0           27
64241    64242.0           27
51373    51374.0           27
50932    50933.0           27
48676    48677.0           27
48289    48290.0           27
47988    47989.0           27
46662    46663.0           27
46469    46470.0           27
40482    40483.0           27
40284    40285.0    

In [38]:
user_same_movies = user_movie_count[user_movie_count["movie_count"] > (len(movies_wtached)*70)/100]["userId"]

In [39]:
user_same_movies.head()

7      8.0
25    26.0
28    29.0
33    34.0
68    69.0
Name: userId, dtype: float64

In [40]:
len(user_same_movies)

8806

# Determination of Similarity

In [41]:
final_df = pd.concat([movies_watched_df[movies_watched_df.index.isin(user_same_movies)],
                      random_user_df[movies_wtached]])

In [42]:
final_df.head()

title   Apollo 13 (1995)  Batman (1989)  Beauty and the Beast (1991)  Beverly Hills Cop III (1994)  Braveheart (1995)  Casper (1995)  Cliffhanger (1993)  Dances with Wolves (1990)  Firm, The (1993)  First Knight (1995)  Forrest Gump (1994)  Fugitive, The (1993)  GoldenEye (1995)  Interview with the Vampire: The Vampire Chronicles (1994)  Johnny Mnemonic (1995)  Judge Dredd (1995)  Jumanji (1995)  Jurassic Park (1993)  Lion King, The (1994)  Mask, The (1994)  Natural Born Killers (1994)  Pocahontas (1995)  Silence of the Lambs, The (1991)  Star Trek: Generations (1994)  Taxi Driver (1976)  True Lies (1994)  Waterworld (1995)
userId                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
8.0                  4.0            4.0                          3.0                           NaN                5.0            NaN                 5.0                        5.0               4.0                  3.0                  5.0                   5.0               4.0                                                4.0                             1.0                 3.0             NaN                   4.0                    4.0               3.0                          5.0                4.0                               5.0                            3.0                 NaN               4.0                3.0
26.0                 4.0            3.0                          5.0                           3.0                4.0            NaN                 3.0                        4.0               3.0                  NaN                  5.0                   4.0               3.0                                                3.0                             NaN                 2.0             NaN                   5.0                    3.0               4.0                          4.0                NaN                               4.0                            3.0                 NaN               3.0                3.0
29.0                 4.0            4.0                          4.0                           3.0                5.0            3.0                 4.0                        4.0               NaN                  3.0                  5.0                   3.0               NaN                                                5.0                             3.0                 4.0             3.0                   5.0                    4.0               3.0                          3.0                NaN                               4.0                            3.0                 NaN               3.0                3.0
34.0                 5.0            4.0                          5.0                           NaN                NaN            3.0                 3.0                        2.0               NaN                  NaN                  5.0                   5.0               5.0                                                NaN                             3.0                 1.0             3.0                   5.0                    4.0               5.0                          NaN                4.0                               NaN                            4.0                 NaN               5.0                5.0
69.0                 3.0            4.0                          3.0                           NaN                3.0            NaN                 NaN                        3.0               3.0           

In [43]:
final_df.shape

(8807, 27)

In [47]:
corr_df = final_df.T.corr().unstack().sort_values().drop_duplicates()

In [48]:
corr_df = pd.DataFrame(corr_df, columns=["corr"])

In [49]:
corr_df.head()

corr
userId   userId           
66208.0  1617.0  -1.000000
86454.0  97250.0 -0.969049
107788.0 1376.0  -0.937385
39399.0  1270.0  -0.922053
114208.0 81822.0 -0.919240

In [50]:
corr_df.index.names = ["user_id_1", "user_id_2"]

In [51]:
corr_df.head()

corr
user_id_1 user_id_2          
66208.0   1617.0    -1.000000
86454.0   97250.0   -0.969049
107788.0  1376.0    -0.937385
39399.0   1270.0    -0.922053
114208.0  81822.0   -0.919240

In [52]:
corr_df = corr_df.reset_index()

In [53]:
corr_df.head()

user_id_1  user_id_2      corr
0    66208.0     1617.0 -1.000000
1    86454.0    97250.0 -0.969049
2   107788.0     1376.0 -0.937385
3    39399.0     1270.0 -0.922053
4   114208.0    81822.0 -0.919240

In [54]:
top_users = corr_df[(corr_df["user_id_1"] == random_user) & (corr_df["corr"] > 0.60)][["user_id_2", "corr"]].reset_index(drop=True)

In [55]:
top_users

user_id_2      corr
0     39484.0  0.604337
1     52890.0  0.620964
2     55672.0  0.621410
3     43168.0  0.621450
4     73477.0  0.621509
5    116303.0  0.626103
6    107889.0  0.633581
7     43296.0  0.643287
8    122218.0  0.650765
9    122218.0  0.650765
10    97956.0  0.664918
11   114465.0  0.666247
12   105890.0  0.681257
13   107408.0  0.694201
14    93948.0  0.699569
15    93948.0  0.699569
16    66437.0  0.779831

In [56]:
top_users = top_users.sort_values(by="corr", ascending=False)

In [57]:
top_users

user_id_2      corr
16    66437.0  0.779831
15    93948.0  0.699569
14    93948.0  0.699569
13   107408.0  0.694201
12   105890.0  0.681257
11   114465.0  0.666247
10    97956.0  0.664918
9    122218.0  0.650765
8    122218.0  0.650765
7     43296.0  0.643287
6    107889.0  0.633581
5    116303.0  0.626103
4     73477.0  0.621509
3     43168.0  0.621450
2     55672.0  0.621410
1     52890.0  0.620964
0     39484.0  0.604337

In [58]:
top_users.rename(columns={"user_id_2": "userId"}, inplace=True)

In [59]:
top_users.head()

userId      corr
16   66437.0  0.779831
15   93948.0  0.699569
14   93948.0  0.699569
13  107408.0  0.694201
12  105890.0  0.681257

In [60]:
top_users_ratings = top_users.merge(ratings[["userId", "movieId", "rating"]], how="inner")

In [61]:
top_users_ratings.head()

userId      corr  movieId  rating
0  66437.0  0.779831        2     4.0
1  66437.0  0.779831        3     3.0
2  66437.0  0.779831        5     3.0
3  66437.0  0.779831        6     4.0
4  66437.0  0.779831        9     3.0

In [62]:
top_users_ratings.shape

(5767, 4)

In [63]:
top_users_rating = top_users_ratings[top_users_ratings["userId"] != random_user]

In [65]:
top_users_rating.head()

userId      corr  movieId  rating
0  66437.0  0.779831        2     4.0
1  66437.0  0.779831        3     3.0
2  66437.0  0.779831        5     3.0
3  66437.0  0.779831        6     4.0
4  66437.0  0.779831        9     3.0

# Calculate Weighted Average Recommendation Score

In [66]:
top_users_ratings["weighted_rating"] = top_users_ratings["corr"] * top_users_ratings["rating"]

In [67]:
top_users_ratings.head()

userId      corr  movieId  rating  weighted_rating
0  66437.0  0.779831        2     4.0         3.119325
1  66437.0  0.779831        3     3.0         2.339494
2  66437.0  0.779831        5     3.0         2.339494
3  66437.0  0.779831        6     4.0         3.119325
4  66437.0  0.779831        9     3.0         2.339494

In [69]:
recommendation_df = top_users_ratings.groupby("movieId").agg({"weighted_rating": "mean"})

In [70]:
recommendation_df.head()

weighted_rating
movieId                 
1               2.267230
2               1.885380
3               1.387313
4               3.406286
5               2.117032

In [71]:
recommendation_df = recommendation_df.reset_index()

In [72]:
recommendation_df.head()

movieId  weighted_rating
0        1         2.267230
1        2         1.885380
2        3         1.387313
3        4         3.406286
4        5         2.117032

In [73]:
recommendation_df[recommendation_df["weighted_rating"] > 3.5]

movieId  weighted_rating
165      306         3.899157
166      307         3.899157
167      308         3.899157
206      371         3.899157

In [74]:
movies_to_be_recommended = recommendation_df[recommendation_df["weighted_rating"] > 3.5].sort_values(by="weighted_rating", ascending=False)

In [75]:
movies_to_be_recommended.head()

movieId  weighted_rating
165      306         3.899157
166      307         3.899157
167      308         3.899157
206      371         3.899157

In [76]:
movies_to_be_recommended.merge(movies[["movieId", "title"]])

movieId  weighted_rating                                             title
0      306         3.899157  Three Colors: Red (Trois couleurs: Rouge) (1994)
1      307         3.899157  Three Colors: Blue (Trois couleurs: Bleu) (1993)
2      308         3.899157   Three Colors: White (Trzy kolory: Bialy) (1994)
3      371         3.899157                                 Paper, The (1994)

# Process Functionalization

In [3]:
def data_prep(data_movie, data_rating, on="movieId"):
    movies = pd.read_csv(data_movie)
    ratings = pd.read_csv(data_rating)
    df = movies.merge(ratings, how="left", on=on)
    return df

In [4]:
df = data_prep("movies.csv", "ratings.csv")

In [5]:
def create_user_movie_df(dataframe):
    rating_counts = pd.DataFrame(dataframe["title"].value_counts())
    rare_movies = rating_counts[rating_counts["title"] < 1000].index
    common_movies = dataframe[~dataframe["title"].isin(rare_movies)]
    user_movie_df = common_movies.pivot_table(index=["userId"], columns=["title"], values="rating")
    return user_movie_df

In [6]:
user_movie_df = create_user_movie_df(df)

In [7]:
def user_based_recommender(random_user, user_movie_df, ratio=0.70, corr_th=0.60, score=3.5):
    random_user_df = user_movie_df[user_movie_df.index == random_user]
    movies_wtached = random_user_df.columns[random_user_df.notna().any()].tolist()
    movies_watched_df = user_movie_df[movies_wtached]
    user_movie_count = movies_watched_df.T.notnull().sum()
    user_movie_count = user_movie_count.reset_index()
    user_movie_count.columns = ["userId", "movie_count"]
    prec = (len(movies_wtached)*ratio)/100
    user_same_movies = user_movie_count[user_movie_count["movie_count"] > prec]["userId"]
    final_df = pd.concat([movies_watched_df[movies_watched_df.index.isin(user_same_movies)],
                      random_user_df[movies_wtached]])
    corr_df = final_df.T.corr().unstack().sort_values().drop_duplicates()
    corr_df = pd.DataFrame(corr_df, columns=["corr"])
    corr_df.index.names = ["user_id_1", "user_id_2"]
    corr_df = corr_df.reset_index()
    top_users = corr_df[(corr_df["user_id_1"] == random_user) & (corr_df["corr"] > corr_th)][["user_id_2", "corr"]].reset_index(drop=True)
    top_users = top_users.sort_values(by="corr", ascending=False)
    top_users.rename(columns={"user_id_2": "userId"}, inplace=True)
    top_users_ratings = top_users.merge(ratings[["userId", "movieId", "rating"]], how="inner")
    top_users_ratings["weighted_rating"] = top_users_ratings["corr"] * top_users_ratings["rating"]
    recommendation_df = top_users_ratings.groupby("movieId").agg({"weighted_rating": "mean"})
    recommendation_df = recommendation_df.reset_index()
    movies_to_be_recommended = recommendation_df[recommendation_df["weighted_rating"] > score].sort_values(by="weighted_rating", ascending=False)
    
    return movies_to_be_recommended.merge(movies[["movieId", "title"]])

In [ ]:
random_user = int(pd.Series(user_movie_df.index).sample(1, random_state=50).values)
user_based_recommender(random_user, user_movie_df, ratio=0.60, corr_th=0.60, score=4)